# Particle database

To install the [expertsystem](expertsystem) in Google Colab, **uncomment** the following:

In [ ]:
# !pip install expertsystem

In PWA, you usually want to search for special resonances, possibly even some not listed in the PDG. In this notebook, we go through a few ways to add or overwrite [Particle](expertsystem.particle.Particle) instances in the database with your own particle definitions.

## Loading the default database

In the [usual workflow](/usage/workflow), you make use of the [StateTransitionManager](expertsystem.reaction.StateTransitionManager). By default, if you do not specify the `particles` argument, the [StateTransitionManager](expertsystem.reaction.StateTransitionManager) calls the function [load_default_particles](expertsystem.reaction.load_default_particles). This functions returns a [ParticleCollection](expertsystem.particle.ParticleCollection) instance with [Particle](expertsystem.particle.Particle) definitions from the [PDG](https://pdg.lbl.gov), along with additional definitions that are provided in the file {download}`additional_particle_definitions.yml <../../src/expertsystem/additional_particle_definitions.yml>`.

Here, we call this method directly to illustrate what happens (we use [io.load_pdg](expertsystem.io.load_pdg), which loads a subset):

In [ ]:
from expertsystem import io

particle_db = io.load_pdg()
print("Number of loaded particles:", len(particle_db))

In the following, we illustrate how to use the methods of the [ParticleCollection](expertsystem.particle.ParticleCollection) class to find and 'modify' [Particle](expertsystem.particle.Particle)s and [add](expertsystem.particle.ParticleCollection.add) them back to the [ParticleCollection](expertsystem.particle.ParticleCollection).

## Finding particles

The [ParticleCollection](expertsystem.particle.ParticleCollection) class offers some methods to search for particles by name or by PID (see [find](expertsystem.particle.ParticleCollection.find)):

In [ ]:
particle_db.find(333)

With [filter](expertsystem.particle.ParticleCollection.filter), you can perform more sophisticated searches. This is done by either passing a function or [lambda](https://docs.python.org/3/tutorial/controlflow.html#lambda-expressions).

In [ ]:
subset = particle_db.filter(lambda p: p.name.startswith("f(2)"))
subset.names

In [ ]:
subset = particle_db.filter(
    lambda p: p.strangeness == 1 and p.spin >= 1 and p.mass > 1.8 and p.mass < 1.9
)
subset.names

In [ ]:
subset = particle_db.filter(lambda p: p.is_lepton())
subset.names

In each of these examples, we call the [names](expertsystem.particle.ParticleCollection.names) property. This is just to only display the names, sorted alphabetically. The full representation of a [ParticleCollection](expertsystem.particle.ParticleCollection) looks like this:

In [ ]:
particle_db.filter(lambda p: p.name.startswith("pi") and len(p.name) == 3)

## Adding custom particle definitions through Python

A quick way to modify or overwrite particles, is through your Python script or notebook. Notice that the instances in the database are [Particle](expertsystem.particle.Particle) instances:

In [ ]:
N1650_plus = particle_db["N(1650)+"]
N1650_plus

The instances in the database are [immutable](https://en.wikipedia.org/wiki/Immutable_object). Therefore, if you want to modify, say, the width, you have to create a new [Particle](expertsystem.particle.Particle) instance from the particle you want to modify and [add](expertsystem.particle.ParticleCollection.add) it back to the database. You can do this with [create_particle](expertsystem.particle.create_particle):

```{margin} Duplicate names or PIDs
The warning that you see here comes from the fact that names and PIDs are considered mere labels of a {obj}`.Particle` instance ― it is defined uniquely only by its quantum numbers, such as {attr}`~.Particle.spin` and {attr}`~.Particle.charge`. 
    
The warning is suppressed in the rest of this page.
```

In [ ]:
from expertsystem.particle import create_particle

new_N1650_plus = create_particle(
    template_particle=N1650_plus, name="Modified N(1650)+", width=0.2
)

particle_db.add(new_N1650_plus)
particle_db["Modified N(1650)+"].width

You often also want to add the antiparticle of the particle you modified to the database. Using [create_antiparticle](expertsystem.particle.create_antiparticle), it is easy to create the corresponding antiparticle object.

In [ ]:
from expertsystem.particle import create_antiparticle

new_N1650_minus = create_antiparticle(new_N1650_plus, new_name="Modified N(1650)-")

particle_db.add(new_N1650_minus)
particle_db["Modified N(1650)-"]

When adding additional particles you may need for your research, it is easiest to work with an existing particle as template. Let's say we want to study $e^+e^-$ collisions of several energies:

````{margin}
```{note}
By convention, the {mod}`expertsystem` uses $\mathrm{GeV}/c^2$ as energy unit.
```
````

In [ ]:
energies_mev = {4180, 4220, 4420, 4600}
template_particle = particle_db["J/psi(1S)"]
for energy_mev in energies_mev:
    energy_gev = energy_mev / 1e3
    new_particle = create_particle(
        template_particle, name=f"EpEm ({energy_mev} MeV)", mass=energy_gev
    )
    particle_db.add(new_particle)
len(particle_db)

In [ ]:
particle_db.filter(lambda p: "EpEm" in p.name).names

## Loading custom definitions from a YAML file

It's also possible to add particles from a config file, with [load_particle_collection](expertsystem.io.load_particle_collection). Existing entries remain and if the imported file of particle definitions contains a particle with the same name, it is overwritten in the database.

It's easiest to work with YAML. Here, we use the provided {download}`additional_particles.yml` example file:

In [ ]:
from expertsystem.io import load_particle_collection

particle_db += load_particle_collection("additional_particles.yml")

## Writing to XML or YAML

You can also dump the existing particle lists to either YAML or XML. You do this with the [io.write](expertsystem.io.write) function.

In [ ]:
io.write(instance=particle_db, filename="dumped_particle_list.xml")
io.write(instance=particle_db, filename="dumped_particle_list.yaml")

Note that the function [write](expertsystem.io.write) can dump any [ParticleCollection](expertsystem.particle.ParticleCollection) to an output file, also a specific subset.

In [ ]:
from expertsystem.particle import ParticleCollection

output = ParticleCollection()
output += particle_db["J/psi(1S)"]
output += particle_db.find(22)  # gamma
output += particle_db.filter(lambda p: p.name.startswith("f(0)"))
output += particle_db["pi0"]
output += particle_db["pi+"]
output += particle_db["pi-"]
io.write(output, "particle_list_selection.yml")
output.names

As a side note, the [expertsystem](expertsystem) provides [JSON schemas](https://json-schema.org) (e.g. {download}`yaml/particle-list.json <../../src/expertsystem/schemas/yaml/particle-list.json>`) to validate your particle list files (see also [jsonschema.validate](jsonschema.validate)):

In [ ]:
import yaml

with open("dumped_particle_list.yaml") as stream:
    definition = yaml.load(stream, Loader=yaml.SafeLoader)
io._yaml.validation.particle_list(definition)

In addition, if you have installed the [expertsystem](expertsystem) in [Editable mode](install:Editable mode) and {ref}`use VSCode <contribute:Visual Studio code>`, your YAML particle list are checked automatically in the GUI.